# SVMによるボクセルごとの学習と識別性能評価（時系列解析）

---
  
引数：div_rest.csv/div_tapping.csvがあるディレクトリまでのパス  
  
---
  
入力：div_rest.csv/div_tapping.csv

---
  
出力：ACCURACY[loo or k_cv]_voxelsRank_SVM.csv　識別性能評価結果一覧  

---  
  
maskで得たボクセルについて．
ボクセルごとに区切られた時系列データをSVMを用いて学習し，交差検証法（k-分割交差検証，leave-one-out交差検証）を用いて識別性能評価を行う
精度でボクセルをソートし，上位20ボクセルの精度を書き出し．  
ベクトル：各ボクセルの区切られた時系列データ


In [1]:
print('############# ML_SVM_voxels.py program excution ##############')

############# ML_SVM_voxels.py program excution ##############


In [2]:
import numpy as np
import pandas as pd
import sys

from sklearn import cross_validation
from sklearn import svm
from sklearn.model_selection import train_test_split

/home/nakayama/.pyenv/versions/anaconda3-5.3.0/lib/python3.7/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


コマンドライン引数でraw_rest.csv/raw_tapping.csvがあるディレクトリまでのパスを取得

In [22]:
#args = sys.argv
#PATH = args[1]

# jupyter notebookのときはここで指定
PATH = '../State-2fe_Brodmann/20181029rn/64ch/8divData/'

# 検証手法
col_name = 'leave-one-out'

# ボクセル数 
voxels = 70455

## SVM_LOO関数
引数として教師データをX，ラベルをyで受け取る．  
交差検証法の一つleave-one-out交差検証で識別精度評価を行う．

* (1個をテストデータ，残りを教師データにして学習・評価) * すべてのデータ個
* 得られたすべてのデータ個の評価結果（識別率）の平均を求めてパーセントに直す
* 評価結果（識別率）をmain関数に返す

In [4]:
def SVM_LOO(X, y):

    LOOscore = np.zeros(len(X))
    
    # 1個をテストデータ，残りを教師データにして学習・評価
    # すべてのデータに対して行う
    for i in range(len(X)):
        
        print('------ ' + str(i + 1) + ' / ' + str(len(X)) + '回 -----')

        # テストデータ
        X_test = X[i].reshape(1, -1)
        y_test = y[i].reshape(1, -1)

        # テストデータとして使用するデータを除いた教師データを作成
        X_train = np.delete(X, i, 0)
        y_train = np.delete(y, i, 0)

        # 線形SVMのインスタンスを生成
        model = svm.SVC(kernel = 'linear', C = 1)
        
        # モデルの学習
        model.fit(X_train, y_train)

        # 評価結果（識別率）を格納
        LOOscore[i] = model.score(X_test, y_test)

        
    # 評価結果（識別率）の平均を求める
    result = LOOscore.mean()
    
    # パーセントに直す
    result = round(result * 100, 1)
    
    print(str(LOOscore) + '\n')

    return result

## SVM_kCV関数
引数とし教師データをX，ラベルをyで受け取る．  
交差検証法の一つk-分割交差検証で識別精度評価を行う．

* 学習
* (k分割し，1グループをテストデータ，残りグループを教師データにして評価) * k
* 得られたk個の評価結果（識別率）の平均を求めてパーセントに直す
* 評価結果（識別率）をmain関数に返す

In [5]:
def SVM_kCV(X, y):
    
    # 線形SVMのインスタンスを生成
    model = svm.SVC(kernel = 'linear', C = 1)
    
    # k分割し，1グループをテストデータ，残りグループを教師データにして評価
    # すべてのグループに対して行う
    # 評価結果（識別率）を格納
    CVscore = cross_validation.cross_val_score(model, X, y, cv = cv_k)
    
    # 評価結果（識別率）の平均を求める
    result = CVscore.mean()
    
    # パーセントに直す
    result = round(result * 100, 1)

    print('k = ' + str(cv_k) + '：' + str(CVscore))
    
    return result
    

## TrainingData関数
引数として読み込みたいタスクごとのデータをreset, tapで受け取る． 
* 機械学習にかけれるようにデータのベクトル化とラベルを作成
* ベクトル化したデータとラベルをmain関数に返す

In [6]:
def TrainingData(rest, tap):

    # 各タスクのデータを縦結合
    all_data = pd.concat([rest, tap], axis = 0)

    # ベクトル化
    X = all_data.as_matrix()

    # ラベル作成 rest = 0, tap = 1
    label_rest = np.zeros(len(rest.index))
    label_tap = np.ones(len(tap.index))

    y = np.r_[label_rest, label_tap]

    
    return X, y

    

## main関数

In [8]:
if __name__ == '__main__':
    
    # 読み込みたいファイルのパス
    PATH_rest = PATH + 'div_rest.csv'
    PATH_tap = PATH + 'div_tapping.csv'

    # csvファイル読み込み
    # headerは設定せず，転置後にset_index()する（header = 0にすると列名が変えられる）
    rest = pd.read_csv(PATH_rest, header = None).T    
    rest = rest.set_index(0)
    
    tap = pd.read_csv(PATH_tap, header = None).T
    tap = tap.set_index(0)

    # 分割数を求める：列数 / ボクセル数
    divNum = len(rest.columns) // voxels
    
    # 全ボクセルの識別率を格納するデータフレーム
    voxAc = pd.DataFrame(index = sorted(list(set(rest.index))), columns = [col_name])

    for i in range(voxels):
        
        print(i)
        
        # ボクセル名
        voxName = 'Voxel' + str(i+1)
        
        print(voxName)
        
        # 各ボクセルごとにデータを取得
        restVox = rest.loc[voxName]
        tapVox = tap.loc[voxName]
        
        
        # データとラベルの準備
        data, labels = TrainingData(restVox, tapVox)
        
        
        # 学習と交差検証
        print('leave-one-out cross-validation')

        result_loo = SVM_LOO(data, labels)
        print(result_loo)

        # データフレームに格納
        voxAc.at[voxName, col_name] = result_loo
        

/home/nakayama/.pyenv/versions/anaconda3-5.3.0/lib/python3.7/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,173,174,175,176,177,178,179,180,181,182,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,238,239,240,241,242,2

0
Voxel1


/home/nakayama/.pyenv/versions/anaconda3-5.3.0/lib/python3.7/site-packages/ipykernel_launcher.py:7: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  import sys


leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 1. 0.]

31.2
1
Voxel2
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0.]

18.8
2
Voxel3
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 

leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 1. 0.]

31.2
22
Voxel23
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0.]

12.5
23
Voxel24
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
---

...

------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 0. 1. 0. 1. 1.]

50.0
9900
Voxel9901
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0. 1. 0. 1. 0.]

31.2
9901
Voxel9902
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 1. 1. 1. 1. 0. 

leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1.]

25.0
9924
Voxel9925
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1.]

25.0
9925
Voxel9926
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -

leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]

18.8
9948
Voxel9949
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 1. 1. 1.]

50.0
9949
Voxel9950
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -

leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 1. 0. 1. 0.]

25.0
9972
Voxel9973
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -----
------ 5 / 16回 -----
------ 6 / 16回 -----
------ 7 / 16回 -----
------ 8 / 16回 -----
------ 9 / 16回 -----
------ 10 / 16回 -----
------ 11 / 16回 -----
------ 12 / 16回 -----
------ 13 / 16回 -----
------ 14 / 16回 -----
------ 15 / 16回 -----
------ 16 / 16回 -----
[0. 0. 0. 1. 1. 1. 0. 0. 1. 1. 0. 0. 1. 0. 0. 1.]

43.8
9973
Voxel9974
leave-one-out cross-validation
------ 1 / 16回 -----
------ 2 / 16回 -----
------ 3 / 16回 -----
------ 4 / 16回 -

KeyError: 'the label [Voxel9985] is not in the [index]'

In [17]:
    # 識別率精度の高い順にソート 
    voxAc=voxAc.sort_values('leave-one-out', ascending=False)


In [21]:
    # csv書き出し
    PATH_RESULT = PATH + 'ACCURACY[loo]_voxels_SVM.csv'
    voxAc.to_csv(PATH_RESULT, index = True)